### **JPMorgan Chase & Co - Quantitative Research**
### Task Four - Use dynamic programming to convert FICO scores into categorical data to predict defaults (Incomplete File)
---

We are tasked to create a rating map that maps the FICO score of the borrowers to a rating where a lower rating signifies a better credit score. We attempt to map all FICO scores to a specific value whilst minimising the mean squared error (MSE).

In [35]:
# Load libraries
import pandas as pd
from math import log
import numpy as np

First we read our loans data

In [29]:
df = pd.read_csv('Loan_Data.csv')

We now create two arrays, one for *x = df['default'].to_list()
y = df['fico_score'].to_list()
n = len(x)
print (len(x), len(y))
defaulting* and the other for *fico_score*. Since our goal is to use FICO scores to predict defaults, we must study these two variables.

In [32]:
x = df['default'].to_list()
y = df['fico_score'].to_list()
n = len(x)
print (len(x), len(y))

10000 10000


We setup two further arrays of length $850$ (as the maximum FICO score) for default and total.

In [40]:
default = [0 for i in range(851)]
total = [0 for i in range(851)]

In [41]:
for i in range(n):
    y[i] = int(y[i])
    default[y[i]-300] += x[i]
    total[y[i]-300] += 1
    
for i in range(0, 551):
    default[i] += default[i-1]
    total[i] += total[i-1]

We define the given log-likelihood function below.

In [42]:
def log_likelihood(n, k):
    p = k/n
    if (p==0 or p==1):
        return 0
    return k*np.log(p)+ (n-k)*np.log(1-p)


In [43]:
r = 10

In [44]:
dp = [[[-10**18, 0] for i in range(551)] for j in range(r+1)]

In [45]:
for i in range(r+1):
    for j in range(551):
        if (i==0):
            dp[i][j][0] = 0
        else:
            for k in range(j):
                if (total[j]==total[k]):
                    continue
                if (i==1):
                    dp[i][j][0] = log_likelihood(total[j], default[j])
                else:
                    if (dp[i][j][0] < (dp[i-1][k][0] + log_likelihood(total[j]-total[k], default[j] - default[k]))):
                        dp[i][j][0] = log_likelihood(total[j]-total[k], default[j]-default[k]) + dp[i-1][k][0]
                        dp[i][j][1] = k
                                                     
print (round(dp[r][550][0], 4))


-4217.8245


In [46]:
k = 550
l = []
while r >= 0:
    l.append(k+300)
    k = dp[r][k][1]
    r -= 1

print(l)


[850, 753, 752, 732, 696, 649, 611, 580, 552, 520, 300]
